# Managing Optimizations and Solutions

LunaSolve lets you securely store all your optimization problems and their corresponding solutions in your account. This allows you to conveniently access your data without managing your results on your local computer. To help organize your data, LunaSolve provides various tools for managing it, including uploading, editing, and deleting optimizations and solutions.

After completing this guide, you will be able to:

1. Manage, modify, and remove your optimizations in LunaSolve.
2. Manage, modify, and remove your solutions in LunaSolve.

First, you'll need to import the necessary packages and initiate your session with LunaSolve.

In [ ]:
# Load the Luna package
from luna_sdk import LunaSolve

# Initialize LunaSolve with your credentials
ls = LunaSolve(email="YOUREMAIL", password="YOURPASSWORD")

## Managing Optimizations

First, you'll need to upload an optimization problem to Luna. In this example, we'll use a simple optimization in the BQM format.

In [ ]:
from luna_sdk.schemas.optimization_formats.bqm import BQMSchema

# Define your QUBO problem as a BQM
bqm_data = {
    "linear": {"0": 4.0, "1": -2.0, "2": 6.0, "3": 2.0, "4": 5.0},
    "quadratic": {("3", "2"): -6.0, ("4", "0"): -4.0},
    "vartype": "BINARY"
}

bqm = BQMSchema(**bqm_data)

# Upload your BQM to LunaSolve
optimization = ls.optimization.create_from_bqm(name="My BQM", bqm=bqm)

Luna makes it easy to manage all your stored optimizations. You can retrieve, edit, and delete them.

In [ ]:
# Retrieve an optimization
optimization = ls.optimization.get(optimization_id=optimization.id)

print(optimization)

In [ ]:
# Retrieve all optimization available to you
ls.optimization.get_all()

In [ ]:
from luna_sdk.schemas.enums.timeframe import TimeframeEnum

# If desired, you can specify a timeframe for when the optimizations were created
# Additionally, you can set a limit on the number of optimizations to be returned, which is set to 50 by default
ls.optimization.get_all(timeframe=TimeframeEnum.this_week, limit=10)

In [ ]:
# Rename an optimization
updated_optimization = ls.optimization.update(optimization_id=optimization.id, name="My Updated BQM")

print(updated_optimization)

In [ ]:
# Delete an optimization
ls.optimization.delete(optimization_id=optimization.id)

## Managing Solutions

First, you'll need to create a solution for an optimization via Luna. We'll use the same BQM from earlier and generate a simple solution using the Simulated Annealing algorithm.

In [ ]:
# Define your QUBO problem as a BQM
bqm_data = {
    "linear": {"0": 4.0, "1": -2.0, "2": 6.0, "3": 2.0, "4": 5.0},
    "quadratic": {("3", "2"): -6.0, ("4", "0"): -4.0},
    "vartype": "BINARY"
}

bqm = BQMSchema(**bqm_data)

# Upload your BQM to LunaSolve
optimization = ls.optimization.create_from_bqm(name="My BQM", bqm=bqm)

# Create a solution for the BQM using SA
job = ls.solution.create(
    optimization_id=optimization.id, 
    solver_name="SA", 
    provider="dwave"
)

Similar to optimizations, Luna provides the same features for managing solutions.

In [ ]:
# Retrieve an optimization
solution = ls.solution.get(solution_id=job.id)

print(solution.head)

In [ ]:
# Retrieve all solutions available to you
ls.solution.get_all()

In [ ]:
# If desired, you can specify a timeframe for when the solutions were created
# Additionally, you can set a limit on the number of solutions to be returned, which is set to 50 by default
ls.solution.get_all(timeframe=TimeframeEnum.this_week, limit=10)

In [ ]:
# Delete a solution
ls.solution.delete(solution_id=job.id)

Because some algorithms return multiple possible solutions, Luna allows you to retrieve only the best result from any created solutions.

In [ ]:
ls.solution.get_best_result(solution)

When you create a solution through our use case library, Luna also offers the option to directly access the best result within the use case representation.

In [ ]:
import networkx as nx
from luna_sdk.schemas import TravellingSalesmanProblem

# Create an empty graph using networkx
graph = nx.Graph()

# Define the cities we want to visit
cities = ['Berlin', 'Hamburg', 'Munich']

# Add the cities as nodes in our graph
graph.add_nodes_from(cities)

# Define the distances between each city
edges = [('Berlin', 'Hamburg', 289),
         ('Berlin', 'Munich', 586),
         ('Hamburg', 'Munich', 796)]

# Add the distances as the edges in our graph
graph.add_weighted_edges_from(edges)

# Convert the networkx graph to a digestible format for Luna
graph_data = nx.to_dict_of_dicts(graph)

# Define that we want to create a TSP with the corresponding graph data
tsp = TravellingSalesmanProblem(graph=graph_data)

# Create a TSP instance and retrieve the corresponding ID
optimization = ls.optimization.create_from_use_case(name="My TSP", use_case=tsp)

# Create a solution for the TSP using SA
job = ls.solution.create(
    optimization_id=optimization.id, 
    solver_name="SA", 
    provider="dwave"
)

# Instead of retrieving the raw solution, get it in the format fitting for your problem formulation
use_case_solution = ls.solution.get_use_case_representation(job.id)

# Finally, get the best result directly in the use case representation
result = ls.solution.get_best_use_case_result(use_case_solution)

print(result)